In [1]:
#pip install rank_bm25


In [2]:
import pandas as pd
from pathlib import Path
from rank_bm25 import BM25Okapi
import datasets

from IPython.display import Image, JSON
from IPython.core.display import HTML
import rich
import re

import nltk.corpus
import nltk
import nltk.stem

#from nltk.corpus import stopwords


In [3]:
nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('omw-1.4')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/jupyter/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to /home/jupyter/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to /home/jupyter/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to /home/jupyter/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

In [4]:
dset = datasets.load_from_disk("../data/processed")

In [5]:
dset

Dataset({
    features: ['photo_id', 'photo_url', 'photo_image_url', 'photo_submitted_at', 'photo_featured', 'photo_width', 'photo_height', 'photo_aspect_ratio', 'photo_description', 'photographer_username', 'photographer_first_name', 'photographer_last_name', 'exif_camera_make', 'exif_camera_model', 'exif_iso', 'exif_aperture_value', 'exif_focal_length', 'exif_exposure_time', 'photo_location_name', 'photo_location_latitude', 'photo_location_longitude', 'photo_location_country', 'photo_location_city', 'stats_views', 'stats_downloads', 'ai_description', 'ai_primary_landmark_name', 'ai_primary_landmark_latitude', 'ai_primary_landmark_longitude', 'ai_primary_landmark_confidence', 'blur_hash', 'description_final', 'image'],
    num_rows: 24995
})

In [6]:
dset['description_final'][:5]

['Woman exploring a forest',
 'Succulents in a terrarium',
 'Rural winter mountainside',
 'Poppy seeds and flowers',
 'Silhouette near dark trees']

In [7]:
corpus = dset['description_final']

In [8]:
def my_awesome_tokenizer(content, min_token_length=2):
    content = content.lower()
    
    # only keep alphanumeric
    content = re.sub(r'\W+', ' ', content)
    
    
    tokens = nltk.word_tokenize(content)
    lemmatizer = nltk.stem.WordNetLemmatizer()
    
    tokens_final = []
    
    for token in tokens:
        if  (   ( len(token) >= min_token_length )  and 
                ( token not in  nltk.corpus.stopwords.words("english")  )  
            ):
            
            token =lemmatizer.lemmatize(token)
            
            tokens_final.append(token)
            
            
    return tokens_final

In [9]:
nltk.word_tokenize("meN shoes")
    

['meN', 'shoes']

In [10]:
re.sub(r'\W+', ' ', "meN 567 ; $ shoes")

'meN 567 shoes'

In [11]:
my_awesome_tokenizer ("meN shoes running ran")

['men', 'shoe', 'running', 'ran']

In [12]:
nltk.corpus.stopwords.words("english") 

['i',
 'me',
 'my',
 'myself',
 'we',
 'our',
 'ours',
 'ourselves',
 'you',
 "you're",
 "you've",
 "you'll",
 "you'd",
 'your',
 'yours',
 'yourself',
 'yourselves',
 'he',
 'him',
 'his',
 'himself',
 'she',
 "she's",
 'her',
 'hers',
 'herself',
 'it',
 "it's",
 'its',
 'itself',
 'they',
 'them',
 'their',
 'theirs',
 'themselves',
 'what',
 'which',
 'who',
 'whom',
 'this',
 'that',
 "that'll",
 'these',
 'those',
 'am',
 'is',
 'are',
 'was',
 'were',
 'be',
 'been',
 'being',
 'have',
 'has',
 'had',
 'having',
 'do',
 'does',
 'did',
 'doing',
 'a',
 'an',
 'the',
 'and',
 'but',
 'if',
 'or',
 'because',
 'as',
 'until',
 'while',
 'of',
 'at',
 'by',
 'for',
 'with',
 'about',
 'against',
 'between',
 'into',
 'through',
 'during',
 'before',
 'after',
 'above',
 'below',
 'to',
 'from',
 'up',
 'down',
 'in',
 'out',
 'on',
 'off',
 'over',
 'under',
 'again',
 'further',
 'then',
 'once',
 'here',
 'there',
 'when',
 'where',
 'why',
 'how',
 'all',
 'any',
 'both',
 'each

In [13]:
#tokenized_corpus = [doc.split(" ") for doc in corpus]

In [14]:
??BM25Okapi

Init signature: BM25Okapi(corpus, tokenizer=None, k1=1.5, b=0.75, epsilon=0.25)
Docstring:      <no docstring>
Source:        
class BM25Okapi(BM25):
    def __init__(self, corpus, tokenizer=None, k1=1.5, b=0.75, epsilon=0.25):
        self.k1 = k1
        self.b = b
        self.epsilon = epsilon
        super().__init__(corpus, tokenizer)

    def _calc_idf(self, nd):
        """
        Calculates frequencies of terms in documents and in corpus.
        This algorithm sets a floor on the idf values to eps * average_idf
        """
        # collect idf sum to calculate an average idf for epsilon value
        idf_sum = 0
        # collect words with negative idf to set them a special epsilon value.
        # idf can be negative if word is contained in more than half of documents
        negative_idfs = []
        for word, freq in nd.items():
            idf = math.log(self.corpus_size - freq + 0.5) - math.log(freq + 0.5)
            self.idf[word] = idf
            idf_sum += idf
 

In [15]:
bm25 = BM25Okapi(corpus=corpus, tokenizer=my_awesome_tokenizer)

In [16]:
rich.print(bm25.idf)

{
    'woman': 3.6223610085515094,
    'exploring': 6.527697529642992,
    'forest': 3.7786194982184664,
    'succulent': 6.306936815102121,
    'terrarium': 8.873568090345968,
    'rural': 7.3224503865599,
    'winter': 4.613304022578405,
    'mountainside': 8.421502939393617,
    'poppy': 6.500628791547307,
    'seed': 7.874799159391333,
    'flower': 2.8776699086146875,
    'silhouette': 4.03708437239102,
    'near': 3.106819006714632,
    'dark': 5.234573498143792,
    'tree': 2.3666205134899414,
    'riding': 6.306936815102121,
    'lesson': 8.873568090345968,
    'mountain': 2.4113250680256373,
    'grass': 3.8159046997351407,
    'morning': 4.969148827655692,
    'sun': 4.75899139978267,
    'glowing': 7.6836638762016545,
    'sky': 3.1485973158581393,
    'ocean': 4.250099319592061,
    'brown': 2.4235688118682326,
    'tent': 5.911639408357204,
    'gray': 3.630282451894124,
    'sunset': 3.6741186628767304,
    'empire': 8.622213649260958,
    'state': 6.306936815102121,
    'building': 4.224451814373456,
    'white': 2.257375627676277,
    'stork': 8.873568090345968,
    'water': 2.7681554420992196,
    'black': 3.0798282381132527,
    'purple': 4.749542947670684,
    'thunderstorm': 7.451742180488658,
    'night': 3.802703139318547,
    'time': 4.23293017703696,
    'calm': 5.399006990555965,
    'body': 3.3681652872515313,
    'alp': 6.055101219394409,
    'nighttime': 5.542710461670582,
    'cloud': 3.8447682868249933,
    'golden': 4.38561773990566,
    'hour': 4.41908356704138,
    'breaking': 7.523241173291561,
    'wave': 4.337381935944496,
    'rolling': 7.385010775566861,
    'beneath': 8.254408838724043,
    'storm': 5.926605172497428,
    'wear': 7.600242241646203,
    'tall': 5.710366810866529,
    'palm': 4.807596914478923,
    'sea': 3.955841145994434,
    'dock': 6.222516141203659,
    'taken': 4.963328179520835,
    'woden': 9.720945971538624,
    'pole': 7.600242241646203,
    'sand': 4.41908356704138,
    'beach': 3.842819026272095,
    'squirrel': 6.613584538893049,
    'walnut': 9.720945971538624,
    'roof': 7.263569852908714,
    'top': 4.78300377525832,
    'view': 3.5958643913214487,
    'daisy': 6.6439299476761295,
    'clump': 8.421502939393617,
    'verdant': 9.210080338170322,
    'mossy': 7.207959966522894,
    'city': 4.754256205238373,
    'light': 4.04651726380148,
    'orange': 4.321794350005299,
    'cloudy': 4.717147587874635,
    'beautiful': 4.685751378512926,
    'urban': 7.155276196203579,
    'make': 5.662860121856805,
    'wish': 7.874799159391333,
    'pink': 3.785970979407172,
    'cluster': 6.96853007725619,
    'green': 2.4643905759084683,
    'field': 3.6129331302704975,
    'group': 6.089967532765188,
    'people': 4.744851422998316,
    'setting': 6.474271415916842,
    'campfire': 7.774675678421795,
    'horse': 4.906888169934921,
    'lake': 4.051266125213729,
    'shore': 4.869168487191605,
    'red': 3.665861961383335,
    'leaf': 3.5790670554686708,
    'concrete': 4.879803298900331,
    'wall': 5.154378594886624,
    'selective': 4.2160426912230555,
    'photography': 2.49297375232221,
    'conifer': 7.6836638762016545,
    'cone': 7.105225737192014,
    'desolate': 7.600242241646203,
    'gerbera': 8.873568090345968,
    'close': 4.00018870295602,
    'cliff': 4.901413070869804,
    'herd': 6.81118430471039,
    'cow': 6.70752346716004,
    'eating': 6.555517157852637,
    'tulip': 5.651325596299145,
    'edge': 6.329200030440802,
    'aerial': 3.630282451894124,
    'snow': 3.3669234213257377,
    'covered': 3.723330049270057,
    'little': 5.407975807765469,
    'peace': 7.3224503865599,
    'slovakia': 8.622213649260958,
    'ii': 8.111267977475617,
    'extremely': 7.874799159391333,
    'delicious': 9.720945971538624,
    'spinach': 9.720945971538624,
    'cake': 8.622213649260958,
    'found': 5.941797089832515,
    'eto': 9.720945971538624,
    'caffe': 9.720945971538624,
    'london': 7.207959966522894,
    'board': 6.6439299476761295,
    'swimming': 5.

In [17]:
rich.print(bm25.idf)

{
    'woman': 3.6223610085515094,
    'exploring': 6.527697529642992,
    'forest': 3.7786194982184664,
    'succulent': 6.306936815102121,
    'terrarium': 8.873568090345968,
    'rural': 7.3224503865599,
    'winter': 4.613304022578405,
    'mountainside': 8.421502939393617,
    'poppy': 6.500628791547307,
    'seed': 7.874799159391333,
    'flower': 2.8776699086146875,
    'silhouette': 4.03708437239102,
    'near': 3.106819006714632,
    'dark': 5.234573498143792,
    'tree': 2.3666205134899414,
    'riding': 6.306936815102121,
    'lesson': 8.873568090345968,
    'mountain': 2.4113250680256373,
    'grass': 3.8159046997351407,
    'morning': 4.969148827655692,
    'sun': 4.75899139978267,
    'glowing': 7.6836638762016545,
    'sky': 3.1485973158581393,
    'ocean': 4.250099319592061,
    'brown': 2.4235688118682326,
    'tent': 5.911639408357204,
    'gray': 3.630282451894124,
    'sunset': 3.6741186628767304,
    'empire': 8.622213649260958,
    'state': 6.306936815102121,
    'building': 4.224451814373456,
    'white': 2.257375627676277,
    'stork': 8.873568090345968,
    'water': 2.7681554420992196,
    'black': 3.0798282381132527,
    'purple': 4.749542947670684,
    'thunderstorm': 7.451742180488658,
    'night': 3.802703139318547,
    'time': 4.23293017703696,
    'calm': 5.399006990555965,
    'body': 3.3681652872515313,
    'alp': 6.055101219394409,
    'nighttime': 5.542710461670582,
    'cloud': 3.8447682868249933,
    'golden': 4.38561773990566,
    'hour': 4.41908356704138,
    'breaking': 7.523241173291561,
    'wave': 4.337381935944496,
    'rolling': 7.385010775566861,
    'beneath': 8.254408838724043,
    'storm': 5.926605172497428,
    'wear': 7.600242241646203,
    'tall': 5.710366810866529,
    'palm': 4.807596914478923,
    'sea': 3.955841145994434,
    'dock': 6.222516141203659,
    'taken': 4.963328179520835,
    'woden': 9.720945971538624,
    'pole': 7.600242241646203,
    'sand': 4.41908356704138,
    'beach': 3.842819026272095,
    'squirrel': 6.613584538893049,
    'walnut': 9.720945971538624,
    'roof': 7.263569852908714,
    'top': 4.78300377525832,
    'view': 3.5958643913214487,
    'daisy': 6.6439299476761295,
    'clump': 8.421502939393617,
    'verdant': 9.210080338170322,
    'mossy': 7.207959966522894,
    'city': 4.754256205238373,
    'light': 4.04651726380148,
    'orange': 4.321794350005299,
    'cloudy': 4.717147587874635,
    'beautiful': 4.685751378512926,
    'urban': 7.155276196203579,
    'make': 5.662860121856805,
    'wish': 7.874799159391333,
    'pink': 3.785970979407172,
    'cluster': 6.96853007725619,
    'green': 2.4643905759084683,
    'field': 3.6129331302704975,
    'group': 6.089967532765188,
    'people': 4.744851422998316,
    'setting': 6.474271415916842,
    'campfire': 7.774675678421795,
    'horse': 4.906888169934921,
    'lake': 4.051266125213729,
    'shore': 4.869168487191605,
    'red': 3.665861961383335,
    'leaf': 3.5790670554686708,
    'concrete': 4.879803298900331,
    'wall': 5.154378594886624,
    'selective': 4.2160426912230555,
    'photography': 2.49297375232221,
    'conifer': 7.6836638762016545,
    'cone': 7.105225737192014,
    'desolate': 7.600242241646203,
    'gerbera': 8.873568090345968,
    'close': 4.00018870295602,
    'cliff': 4.901413070869804,
    'herd': 6.81118430471039,
    'cow': 6.70752346716004,
    'eating': 6.555517157852637,
    'tulip': 5.651325596299145,
    'edge': 6.329200030440802,
    'aerial': 3.630282451894124,
    'snow': 3.3669234213257377,
    'covered': 3.723330049270057,
    'little': 5.407975807765469,
    'peace': 7.3224503865599,
    'slovakia': 8.622213649260958,
    'ii': 8.111267977475617,
    'extremely': 7.874799159391333,
    'delicious': 9.720945971538624,
    'spinach': 9.720945971538624,
    'cake': 8.622213649260958,
    'found': 5.941797089832515,
    'eto': 9.720945971538624,
    'caffe': 9.720945971538624,
    'london': 7.207959966522894,
    'board': 6.6439299476761295,
    'swimming': 5.

In [18]:
dset.select([1])[0]['description_final']

'Succulents in a terrarium'

In [19]:
JSON (bm25.doc_freqs[1])

<IPython.core.display.JSON object>

In [20]:
JSON (bm25.doc_freqs)

<IPython.core.display.JSON object>

In [21]:
def find_results(query:str , k =5):
    
    tokenized_query = my_awesome_tokenizer(query)
    doc_scores = bm25.get_scores(tokenized_query)
    
    tokens_in_vocab = [ token for token in tokenized_query  if token in bm25.idf]
    top_items = doc_scores.argsort()[-k:][::-1]
    
    degug_info = {
         "query_original":  query 
         , "tokenized_query":  tokenized_query 
         , "tokens_in_vocab" : tokens_in_vocab
        , "doc_scores":  doc_scores 
        , "top_items":  top_items 
    }
    rich.print (degug_info )
    

    display(HTML(f"<h1>Query: {query} </h1>"))
    
    # Iterate over the top k results
    for idx, photo_data in enumerate( dset.select(top_items)):
        
        doc_idx = top_items[idx]
        # Display the photo
        display(Image(url=photo_data["photo_image_url"] + "?w=200"))

        # Display the attribution text
        display(HTML(f"""
                     Photo title: {photo_data["description_final"]}   <br/>
                     Photo by <a href="https://unsplash.com/@{photo_data["photographer_username"]}?utm_source=NaturalLanguageImageSearch&utm_medium=referral">{photo_data["photographer_first_name"]} {photo_data["photographer_last_name"]}</a> on <a href="https://unsplash.com/?utm_source=SearchWorkshop&utm_medium=referral">Unsplash</a> <br/>
                     Distance: {doc_scores[doc_idx]}
                     """
                                        ))
        print()

In [22]:
find_results( "Two dogs playing in the snow")

{
    'query_original': 'Two dogs playing in the snow',
    'tokenized_query': ['two', 'dog', 'playing', 'snow'],
    'tokens_in_vocab': ['two', 'dog', 'playing', 'snow'],
    'doc_scores': array([0., 0., 0., ..., 0., 0., 0.]),
    'top_items': array([ 1975, 19267, 19320, 12663, 12209])
}

In [23]:
find_results( "boy and girl on a beach")

{
    'query_original': 'boy and girl on a beach',
    'tokenized_query': ['boy', 'girl', 'beach'],
    'tokens_in_vocab': ['boy', 'girl', 'beach'],
    'doc_scores': array([0., 0., 0., ..., 0., 0., 0.]),
    'top_items': array([23946, 14566, 17981,  5807, 20944])
}

In [24]:
find_results( "image of a man in a desert")

{
    'query_original': 'image of a man in a desert',
    'tokenized_query': ['image', 'man', 'desert'],
    'tokens_in_vocab': ['image', 'man', 'desert'],
    'doc_scores': array([0., 0., 0., ..., 0., 0., 0.]),
    'top_items': array([24413, 15746,  7556,  6959, 19330])
}

In [25]:
%%timeit
search_query = "Two dogs playing in the snow"
k =5 
tokenized_query = my_awesome_tokenizer(search_query)

doc_scores = bm25.get_scores(tokenized_query )

top_items = doc_scores.argsort()[-k:][::-1]



22.4 ms ± 370 µs per loop (mean ± std. dev. of 7 runs, 10 loops each)
